In [1]:
import pandas as pd
import pymongo
import json
import pymongo

In [3]:
client = pymongo.MongoClient("mongodb://localhost:27017")
db = client["project_360_demo"]  # Change to your desired database name
collection = db["competitions"]  # Change to your desired collection name

In [4]:
with open("open-data/data/competitions.json", "r") as file:
    data = json.load(file)
comp_df = pd.read_json("open-data/data/competitions.json")
comp_df.head()

competition_id  season_id country_name        competition_name  \
0               9        281      Germany           1. Bundesliga   
1               9         27      Germany           1. Bundesliga   
2            1267        107       Africa  African Cup of Nations   
3              16          4       Europe        Champions League   
4              16          1       Europe        Champions League   

  competition_gender  competition_youth  competition_international  \
0               male              False                      False   
1               male              False                      False   
2               male              False                       True   
3               male              False                      False   
4               male              False                      False   

  season_name               match_updated           match_updated_360  \
0   2023/2024  2024-07-15T14:15:54.671676  2024-07-15T14:17:00.877356   
1   2015/2016  2024-05-19T11:11:14.192381                        None   
2        2023  2024-06-13T07:51:02.452825                        None   
3   2018/2019  2024-06-12T07:44:38.559714     2021-06-13T16:17:31.694   
4   2017/2018  2024-02-13T02:35:28.134882     2021-06-13T16:17:31.694   

          match_available_360             match_available  
0  2024-07-15T14:17:00.877356  2024-07-15T14:15:54.671676  
1                        None  2024-05-19T11:11:14.192381  
2                        None  2024-06-13T07:51:02.452825  
3                        None  2024-06-12T07:44:38.559714  
4                        None  2024-02-13T02:35:28.134882

In [4]:
collection.insert_many(data)

print("JSON data inserted into MongoDB successfully.")

JSON data inserted into MongoDB successfully.


In [9]:
comp_id = 55
season_id = 43

In [5]:
db['lineups'].drop()
db['events'].drop()
db['three-sixty'].drop()
db['matches'].drop()

In [6]:
import json
from pymongo import MongoClient

def data_loader(comp_id, season_id):
    """
    Loads match data, lineups, events, and 360-degree data from JSON files into a MongoDB database.
    
    Parameters:
    - comp_id (int): The competition ID for the matches.
    - season_id (int): The season ID for the matches.
    
    This function performs the following steps:
    1. Loads match data from a JSON file specified by the competition and season IDs.
    2. Adds competition and season IDs to each match record.
    3. Inserts the match records into the 'matches' collection in the MongoDB database.
    4. Retrieves match IDs from the 'matches' collection.
    5. For each match ID, attempts to load and insert lineups, events, and 360-degree data from respective JSON files into their corresponding collections.
    6. Handles cases where the JSON file for 360-degree data does not exist by printing an error message.
    """
    
    # Define the file paths for matches, lineups, events, and 360-degree data
    matches_filename = f'open-data/data/matches/{comp_id}/{season_id}.json'
    lineups_dir = 'open-data/data/lineups'
    events_dir = 'open-data/data/events'
    three_sixty_dir = 'open-data/data/three-sixty'
    
    # Load match data from the JSON file
    with open(matches_filename, "r", encoding="utf8") as file:
        data = json.load(file)
    
    # Add competition and season IDs to each match record
    for match in data:
        match['competition_id'] = comp_id
        match['season_id'] = season_id
    
    # Insert match records into the 'matches' collection
    collection = db["matches"]
    collection.insert_many(data)
    
    # Query the 'matches' collection to get the match IDs for the given competition and season
    query = {"competition_id": comp_id, "season_id": season_id}
    match_ids = [doc['match_id'] for doc in collection.find(query)]
    
    # Process each match ID to load and insert lineups, events, and 360-degree data
    for match_id in match_ids:
        # Define file paths for lineups, events, and 360-degree data for the current match ID
        lineups_filename = f'{lineups_dir}/{match_id}.json'
        event_filename = f'{events_dir}/{match_id}.json'
        three_sixty_filename = f'{three_sixty_dir}/{match_id}.json'
        
        # Dictionary mapping data types to their corresponding file paths
        filenames = {
            'lineups': lineups_filename,
            'events': event_filename,
            'three-sixty': three_sixty_filename
        }
        
        # Load and insert data for each type
        for key, value in filenames.items():
            try:
                # Open and load the JSON data
                with open(value, "r", encoding="utf8") as file:
                    data = json.load(file)
                
                # Add match ID to each record in the data
                for record in data:
                    record['match_id'] = match_id
                
                # Insert data into the corresponding collection in the database
                collection = db[key]
                collection.insert_many(data)
            except FileNotFoundError:
                # Handle the case where the JSON file does not exist
                print(f'NO {key} data for match ID {match_id}')


In [7]:
for index,row in comp_df.iterrows():
    data_loader(row['competition_id'],row['season_id'])

[{'match_id': 3895302, 'match_date': '2024-04-14', 'kick_off': '17:30:00.000', 'competition': {'competition_id': 9, 'country_name': 'Germany', 'competition_name': '1. Bundesliga'}, 'season': {'season_id': 281, 'season_name': '2023/2024'}, 'home_team': {'home_team_id': 904, 'home_team_name': 'Bayer Leverkusen', 'home_team_gender': 'male', 'home_team_group': None, 'country': {'id': 85, 'name': 'Germany'}, 'managers': [{'id': 1000310, 'name': 'Xabier Alonso Olano', 'nickname': 'Xabi Alonso', 'dob': '1981-11-25', 'country': {'id': 214, 'name': 'Spain'}}]}, 'away_team': {'away_team_id': 176, 'away_team_name': 'Werder Bremen', 'away_team_gender': 'male', 'away_team_group': None, 'country': {'id': 85, 'name': 'Germany'}, 'managers': [{'id': 4057, 'name': 'Ole Werner', 'nickname': None, 'dob': '1988-05-04', 'country': {'id': 85, 'name': 'Germany'}}]}, 'home_score': 5, 'away_score': 0, 'match_status': 'available', 'match_status_360': 'available', 'last_updated': '2024-05-10T16:57:53.017895', 'l